In [1]:
import numpy as np
import tensorflow as tf

C:\Users\lifebloom\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
tf.logging.set_verbosity(tf.logging.INFO)

In [3]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2 and Pooling Layer #2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Dense Layer
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits Layer
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [9]:
# Load training and eval data
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use urllib or similar directly.
Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data\train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data\t10k-labels-idx1-u

In [10]:
# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000001A318528E10>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


In [11]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

In [12]:
# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:probabilities = [[0.09315743 0.10606211 0.10420374 0.09038261 0.09645536 0.10399557
  0.09574243 0.11800408 0.09674612 0.0952506 ]
 [0.10062756 0.09504229 0.09744381 0.10029935 0.09658796 0.10270997
  0.10205623 0.10133193 0.09953631 0.10436463]
 [0.09522825 0.11562279 0.1053924  0.08815467 0.09605604 0.10010193
  0.09269076 0.10360938 0.10507903 0.0980647 ]
 [0.09626044 0.10467217 0.08961039 0.08899458 0.09919962 0.10070667
  0.1031201  0.09680913 0.11072972 0.10989717]
 [0.0964663  0.10945614 0.08738951 0.08993053 0.10463312 0.10376982
  0.10258456 0.09926555 0.10736109 0.09914336]
 [0.0939187  0.11174636 0.10874795 0.08550157 0.09281297 0.10822422
  0.0

INFO:tensorflow:loss = 2.3047879, step = 1
INFO:tensorflow:probabilities = [[0.09422061 0.09691367 0.0942423  0.1092365  0.09137286 0.10578024
  0.10463157 0.10000336 0.09691218 0.10668673]
 [0.09413627 0.10561745 0.09626164 0.10155031 0.10300318 0.10382961
  0.09759416 0.10098549 0.10783626 0.08918558]
 [0.09728648 0.11202607 0.09895722 0.09536655 0.09554474 0.09741411
  0.09592508 0.0988049  0.11805332 0.09062151]
 [0.10061647 0.09840227 0.10886547 0.10250799 0.0892466  0.09783133
  0.09636575 0.09744301 0.11274344 0.0959776 ]
 [0.09957614 0.10497074 0.09381407 0.08681864 0.10103253 0.10397983
  0.10642932 0.10333819 0.10486095 0.09517955]
 [0.09347203 0.10307517 0.10094556 0.09482664 0.10365245 0.10266145
  0.09788538 0.10365808 0.10592376 0.09389944]
 [0.09392898 0.09953133 0.09728058 0.10242193 0.09853121 0.1019325
  0.10406254 0.09368911 0.10630681 0.10231496]
 [0.09311283 0.08971123 0.09705029 0.1057142  0.10016146 0.09825495
  0.09722921 0.09943235 0.10359988 0.11573362]
 [0.09

INFO:tensorflow:global_step/sec: 7.26791
INFO:tensorflow:probabilities = [[0.09214261 0.11017925 0.11551756 0.09245938 0.08513477 0.09305446
  0.10621187 0.10429863 0.1147556  0.08624592]
 [0.09235226 0.09928354 0.09359882 0.09709935 0.09454311 0.10034759
  0.09977648 0.11144325 0.11730034 0.09425534]
 [0.09489515 0.09410796 0.09399367 0.10492875 0.10650263 0.10179177
  0.09576809 0.09604061 0.10547505 0.10649636]
 [0.09721498 0.11061405 0.1043892  0.09157477 0.09947333 0.10631264
  0.0992565  0.08840327 0.11032202 0.09243931]
 [0.10440148 0.11286932 0.10485507 0.09352762 0.09352941 0.10066263
  0.09133814 0.09579096 0.10639673 0.09662864]
 [0.09739897 0.11169378 0.08747475 0.10014414 0.10562292 0.09944571
  0.10269575 0.09684603 0.10118929 0.09748867]
 [0.09328544 0.11130887 0.09758525 0.10077655 0.08807114 0.10998053
  0.09846551 0.0990662  0.10442254 0.09703791]
 [0.09392297 0.10796124 0.08403971 0.10393436 0.09649888 0.09765446
  0.10874195 0.09885493 0.10341669 0.10497473]
 [0.092

INFO:tensorflow:loss = 2.2954755, step = 101 (13.759 sec)
INFO:tensorflow:probabilities = [[0.0945528  0.10884517 0.0983647  0.08657754 0.09350383 0.11494486
  0.09454319 0.10212968 0.11508068 0.09145749]
 [0.08825598 0.10764638 0.10398196 0.09410359 0.093709   0.10664913
  0.10098144 0.09873475 0.10149279 0.1044449 ]
 [0.10624267 0.09425377 0.10320804 0.10067012 0.09822892 0.0984176
  0.10065047 0.09768865 0.10360698 0.09703275]
 [0.10502455 0.10302737 0.09394272 0.09438307 0.0967257  0.09391585
  0.0944261  0.10377802 0.1056811  0.10909545]
 [0.10242489 0.10169922 0.09146073 0.09490597 0.105402   0.09929156
  0.09652497 0.09778175 0.1120137  0.09849519]
 [0.0894827  0.10645141 0.09399022 0.107233   0.09228405 0.09603381
  0.10811532 0.10539567 0.10466723 0.09634663]
 [0.10852271 0.10018294 0.10105936 0.08912478 0.089173   0.10800209
  0.0944919  0.10144352 0.10923754 0.09876215]
 [0.10000668 0.10005531 0.10357168 0.10089476 0.09634299 0.09049544
  0.09739192 0.09646838 0.10850327 0.1

INFO:tensorflow:global_step/sec: 7.30455
INFO:tensorflow:probabilities = [[0.09107755 0.10495593 0.09336302 0.0945918  0.0962424  0.09708893
  0.09867492 0.10341813 0.11187917 0.10870811]
 [0.09563928 0.09484138 0.09902578 0.09208418 0.10201465 0.09886476
  0.10868264 0.09916624 0.11166371 0.09801731]
 [0.09362892 0.10489847 0.10635055 0.10362443 0.09360571 0.09718081
  0.10089205 0.08987444 0.11557691 0.09436772]
 [0.08976056 0.09276363 0.09616236 0.11138934 0.09629329 0.10412212
  0.09839163 0.1017454  0.10029214 0.10907958]
 [0.10532034 0.09719331 0.09791534 0.08771375 0.10056923 0.10027521
  0.09513821 0.09871304 0.11314761 0.10401406]
 [0.09297499 0.11327245 0.10251623 0.10186167 0.09563233 0.09692807
  0.09594444 0.10639911 0.10129686 0.09317389]
 [0.08826353 0.10664555 0.09925361 0.09659542 0.10494906 0.10023706
  0.09643499 0.09573965 0.10466    0.10722105]
 [0.09272176 0.10779814 0.10083832 0.10051798 0.09025959 0.10519471
  0.10927682 0.10343398 0.09842639 0.09153228]
 [0.099

...

INFO:tensorflow:global_step/sec: 7.30028
INFO:tensorflow:probabilities = [[0.99378693 0.00000035 0.00042878 0.00119431 0.00000005 0.00421294
  0.00000924 0.00000957 0.00017548 0.00018242]
 [0.00050749 0.00001355 0.00007441 0.00216302 0.04487362 0.00471903
  0.00000852 0.05061066 0.00007287 0.89695686]
 [0.9999763  0.         0.00001088 0.0000001  0.         0.00000242
  0.0000007  0.00000156 0.00000386 0.00000424]
 [0.00035909 0.00000009 0.0000408  0.00000381 0.0011816  0.01223676
  0.984777   0.00000005 0.00136987 0.00003102]
 [0.00004064 0.00731656 0.678244   0.01873093 0.00012129 0.00088121
  0.00005099 0.23588711 0.05856215 0.00016512]
 [0.00000409 0.00000006 0.00001599 0.00010396 0.00463532 0.00000357
  0.00000051 0.00036829 0.00026665 0.9946016 ]
 [0.00000137 0.00000181 0.00009642 0.00000001 0.00000998 0.0000091
  0.9998696  0.         0.00001155 0.0000001 ]
 [0.00445289 0.00000873 0.05357648 0.00311412 0.00115458 0.00008942
  0.00001146 0.14780112 0.00068562 0.78910565]
 [0.0000

INFO:tensorflow:loss = 0.1479973, step = 19801 (13.700 sec)
INFO:tensorflow:probabilities = [[0.00095597 0.00060378 0.00073459 0.00529107 0.00003519 0.99163014
  0.00054444 0.00001341 0.00008108 0.00011029]
 [0.00001936 0.0000049  0.00006176 0.00000572 0.00000427 0.00010274
  0.00000982 0.00000045 0.99976915 0.00002183]
 [0.00004973 0.99733764 0.00149856 0.00004585 0.00042505 0.0000022
  0.00002609 0.00037643 0.00023623 0.00000224]
 [0.00000306 0.00010076 0.00021325 0.9973793  0.00000184 0.00219826
  0.00000081 0.00000076 0.00006728 0.00003476]
 [0.00006384 0.00002107 0.00014977 0.97614086 0.00017943 0.01033732
  0.0000009  0.00019488 0.00113366 0.01177825]
 [0.00092463 0.00134571 0.00006999 0.01845792 0.00000023 0.96967643
  0.00008118 0.00009353 0.00754784 0.00180259]
 [0.00005316 0.00024221 0.00235348 0.00010119 0.9899866  0.00010303
  0.00588846 0.00034402 0.00015737 0.0007705 ]
 [0.99903166 0.00000003 0.00002768 0.00000574 0.         0.00046901
  0.00000027 0.00043742 0.0000025  0

INFO:tensorflow:global_step/sec: 7.19987
INFO:tensorflow:probabilities = [[0.9997758  0.00000023 0.00014305 0.00002185 0.         0.00005024
  0.00000228 0.00000116 0.00000418 0.00000122]
 [0.00039738 0.00481594 0.00228251 0.0031007  0.00630387 0.9799146
  0.0008362  0.00037848 0.00171168 0.00025861]
 [0.00054709 0.01067585 0.00863535 0.00026817 0.0013815  0.00238732
  0.8918811  0.00001196 0.08418153 0.00003018]
 [0.00003233 0.         0.00000002 0.00000307 0.0000151  0.00000946
  0.00000001 0.9993118  0.00000015 0.00062805]
 [0.00000085 0.00000158 0.00006889 0.00000002 0.00002759 0.00075328
  0.9991314  0.00000001 0.00001644 0.00000002]
 [0.00000295 0.00005353 0.00177019 0.00302321 0.9831691  0.00425558
  0.0002829  0.00117418 0.00074895 0.0055196 ]
 [0.00002119 0.00012682 0.00020517 0.9554598  0.00001613 0.03242182
  0.00000006 0.00176206 0.00174948 0.00823754]
 [0.00480066 0.00009329 0.05275229 0.03626528 0.00212365 0.03776985
  0.00027182 0.01210281 0.6236294  0.23019095]
 [0.0000

INFO:tensorflow:loss = 0.18062225, step = 19901 (13.888 sec)
INFO:tensorflow:probabilities = [[0.00000979 0.00000006 0.00000035 0.00000425 0.00025819 0.00001437
  0.         0.99576133 0.00000045 0.00395122]
 [0.19393207 0.0026531  0.01865074 0.07119735 0.03883064 0.00396657
  0.00512521 0.00395118 0.56937706 0.09231613]
 [0.00000069 0.99670154 0.00002533 0.00128699 0.00013014 0.00004265
  0.00003464 0.00022845 0.0010153  0.00053418]
 [0.00000089 0.00246178 0.00028624 0.00224331 0.34621224 0.00041952
  0.00011083 0.00008658 0.01602064 0.63215804]
 [0.00057792 0.00000146 0.00005744 0.00000021 0.8562267  0.00003301
  0.03541306 0.00000276 0.10750042 0.0001871 ]
 [0.00013823 0.00000006 0.00000711 0.00046036 0.00000275 0.7797134
  0.00054095 0.00000001 0.21912456 0.00001259]
 [0.00009001 0.00000032 0.00034    0.00000133 0.00000011 0.00002756
  0.00000029 0.00000297 0.9995146  0.00002287]
 [0.00073399 0.00218209 0.00376961 0.0485381  0.00001535 0.9327644
  0.00255598 0.00004648 0.00902017 0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.1108124.


In [13]:
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-06-01-12:44:20
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-06-01-12:44:25
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9676, global_step = 20000, loss = 0.10397614
{'accuracy': 0.9676, 'loss': 0.10397614, 'global_step': 20000}
